In [ ]:
import pyspark
import pandas as pd
import numpy as np

import altair as alt



### Data sources provide API Data retrieved in Databricks both as pandas dataftame and Spark dataframe converted to CSV.
- In the case of Spark files, the parquet files were coalesced into one file and saved into the CSV

##### SOURCE LINKS
-https://data.cnra.ca.gov/dataset/well-completion-reports
-https://data.ca.gov/dataset/household-water-supply-shortage-reporting-system-data
-https://data.cnra.ca.gov/dataset/periodic-groundwater-level-measurements



##### DATABRICKS AND DEEPNOTE

- The data was read using API calls from CNRA well water pages. On an average about 5000 records were retrieved and the rest in chunks and placed into an extending list. At this point we have two options. We can convert the entire list to a dataframe and save as CSV in Databricks or Deepnote and use it OR the list can be converted, row by row into spark dataframe and saved as CSV. 
- Pandas dataframe saved as CSV should be read back as Pandas DF.
- Spark dataframe saved as CSV should be read back as Spark dataframe or else you will encounter read error
- Dockerfile and init.py are set in Deepnote so that Spark can be used. 

In [ ]:
pd_df_wellcompletion = pd.read_csv("wellcompletion.csv")

/shared-libs/python3.7/py-core/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3186: DtypeWarning: Columns (1,6,31) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [ ]:
pd_df_wellcompletion

Unnamed: 0 DECIMALLATITUDE  \
0                 0             NaN   
1                 1       37.532473   
2                 2        37.52371   
3                 3       37.696685   
4                 4         37.4315   
...             ...             ...   
1043027     1043027       38.751944   
1043028     1043028       38.848056   
1043029     1043029       38.996667   
1043030     1043030       37.506593   
1043031     1043031       38.159722   

                                          WORKFLOWSTATUS LLACCURACY  \
0                                                    NaN        NaN   
1                                                    NaN     >50 FT   
2                                                    NaN    Unknown   
3                                                    NaN    Unknown   
4        Completeness Review - Auto-Complete - 06-JAN-20        NaN   
...                                                  ...        ...   
1043027                                              NaN    Unknown   
1043028                                              NaN    Unknown   
1043029                                              NaN    Unknown   
1043030                                              NaN    Unknown   
1043031                                              NaN    Unknown   

        PERMITDATE  PUMPTESTLENGTH    SECTION  \
0              NaN             NaN  NO NUMBER   
1              NaN             NaN         03   
2              NaN             NaN         02   
3              NaN             NaN         01   
4        6/21/2019             4.0         09   
...            ...             ...        ...   
1043027        NaN             NaN         35   
1043028        NaN             NaN         35   
1043029        NaN             NaN         03   
1043030        NaN             NaN         11   
1043031        NaN             NaN         31   

                            REGIONOFFICE     DRILLINGMETHOD OTHEROBSERVATIONS  \
0                                    NaN                NaN               NaN   
1        DWR North Central Region Office                NaN               NaN   
2        DWR North Central Region Office              SONIC               NaN   
3        DWR North Central Region Office                NaN               NaN   
4        DWR North Central Region Office      Direct Rotary               NaN   
...                                  ...                ...               ...   
1043027                              NaN                DHD               NaN   
1043028                              NaN         CABLE TOOL               NaN   
1043029                              NaN                HSA               NaN   
1043030                              NaN  HOLLOW STEM AUGER               NaN   
1043031                              NaN      DIRECT ROTARY               NaN   

         ... TOTALCOMPLETEDDEPTH OWNERASSIGNEDWELLNUMBER COUNTYNAME  RANGE  \
0        ...                 NaN                     NaN        NaN    NaN   
1        ...                55.0                   MW-10    Alameda    01W   
2        ...                18.1                 INJ-B11    Alameda    02W   
3        ...                20.0                   UST-1    Alameda    01W   
4        ...               840.0                       2    Alameda    02W   
...      ...                 ...                     ...        ...    ...   
1043027  ...               220.0                       4        NaN    13E   
1043028  ...               250.0                     NaN        NaN    04E   
1043029  ...                60.0                   MW-7S        NaN    10E   
1043030  ...                 NaN                    OHO3        NaN    01W   
1043031  ...               230.0                     NaN        NaN    06E   

        BASELINEMERIDIAN  RECEIVEDDATE  \
0                    NaN           NaN   
1           Mount Diablo           NaN   
2           Mount Diablo           NaN   
3           Mount Di

In [ ]:
_deepnote_run_altair(pd_df_wellcompletion, """{"$schema":"https://vega.github.io/schema/vega-lite/v4.json","mark":{"type":"bar","tooltip":{"content":"data"}},"height":220,"autosize":{"type":"fit"},"data":{"name":"placeholder"},"encoding":{"x":{"field":"PERMITDATE","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}},"y":{"field":"PUMPTESTLENGTH","type":"quantitative","sort":null,"scale":{"type":"linear","zero":true}},"color":{"field":"","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}}}}""")

alt.Chart(...)

In [ ]:
pd_df_wellcompletion.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1043032 entries, 0 to 1043031
Data columns (total 47 columns):
 #   Column                        Non-Null Count    Dtype  
---  ------                        --------------    -----  
 0   Unnamed: 0                    1043032 non-null  int64  
 1   DECIMALLATITUDE               988400 non-null   object 
 2   WORKFLOWSTATUS                74215 non-null    object 
 3   LLACCURACY                    906814 non-null   object 
 4   PERMITDATE                    74088 non-null    object 
 5   PUMPTESTLENGTH                66524 non-null    float64
 6   SECTION                       1007212 non-null  object 
 7   REGIONOFFICE                  1042414 non-null  object 
 8   DRILLINGMETHOD                534724 non-null   object 
 9   OTHEROBSERVATIONS             25851 non-null    object 
 10  WELLYIELDUNITOFMEASURE        222689 non-null   object 
 11  WELLLOCATION                  511443 non-null   object 
 12  PERMITNUMBER                

In [ ]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.getOrCreate()

RuntimeError: Java gateway process exited before sending its port number

In [ ]:
# Reading csv file
# File location and type
file_location = "spark_df_shortage.csv"
file_type = "csv"

# CSV options
infer_schema = "false"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
spark_df_shortage = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

#display(spark_df_shortage)

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=b042e2da-6536-449d-95b8-d85fa08825de' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>